# Computer Vision Nanodegree

## Project: Image Captioning

---

In this notebook, you will train your CNN-RNN model.  

You are welcome and encouraged to try out many different architectures and hyperparameters when searching for a good model.

This does have the potential to make the project quite messy!  Before submitting your project, make sure that you clean up:
- the code you write in this notebook.  The notebook should describe how to train a single CNN-RNN architecture, corresponding to your final choice of hyperparameters.  You should structure the notebook so that the reviewer can replicate your results by running the code in this notebook.  
- the output of the code cell in **Step 2**.  The output should show the output obtained when training the model from scratch.

This notebook **will be graded**.  

Feel free to use the links below to navigate the notebook:
- [Step 1](#step1): Training Setup
- [Step 2](#step2): Train your Model
- [Step 3](#step3): (Optional) Validate your Model

<a id='step1'></a>
## Step 1: Training Setup

In this step of the notebook, you will customize the training of your CNN-RNN model by specifying hyperparameters and setting other options that are important to the training procedure.  The values you set now will be used when training your model in **Step 2** below.

You should only amend blocks of code that are preceded by a `TODO` statement.  **Any code blocks that are not preceded by a `TODO` statement should not be modified**.

### Task #1

Begin by setting the following variables:
- `batch_size` - the batch size of each training batch.  It is the number of image-caption pairs used to amend the model weights in each training step. 
- `vocab_threshold` - the minimum word count threshold.  Note that a larger threshold will result in a smaller vocabulary, whereas a smaller threshold will include rarer words and result in a larger vocabulary.  
- `vocab_from_file` - a Boolean that decides whether to load the vocabulary from file. 
- `embed_size` - the dimensionality of the image and word embeddings.  
- `hidden_size` - the number of features in the hidden state of the RNN decoder.  
- `num_epochs` - the number of epochs to train the model.  We recommend that you set `num_epochs=3`, but feel free to increase or decrease this number as you wish.  [This paper](https://arxiv.org/pdf/1502.03044.pdf) trained a captioning model on a single state-of-the-art GPU for 3 days, but you'll soon see that you can get reasonable results in a matter of a few hours!  (_But of course, if you want your model to compete with current research, you will have to train for much longer._)
- `save_every` - determines how often to save the model weights.  We recommend that you set `save_every=1`, to save the model weights after each epoch.  This way, after the `i`th epoch, the encoder and decoder weights will be saved in the `models/` folder as `encoder-i.pkl` and `decoder-i.pkl`, respectively.
- `print_every` - determines how often to print the batch loss to the Jupyter notebook while training.  Note that you **will not** observe a monotonic decrease in the loss function while training - this is perfectly fine and completely expected!  You are encouraged to keep this at its default value of `100` to avoid clogging the notebook, but feel free to change it.
- `log_file` - the name of the text file containing - for every step - how the loss and perplexity evolved during training.

If you're not sure where to begin to set some of the values above, you can peruse [this paper](https://arxiv.org/pdf/1502.03044.pdf) and [this paper](https://arxiv.org/pdf/1411.4555.pdf) for useful guidance!  **To avoid spending too long on this notebook**, you are encouraged to consult these suggested research papers to obtain a strong initial guess for which hyperparameters are likely to work best.  Then, train a single model, and proceed to the next notebook (**3_Inference.ipynb**).  If you are unhappy with your performance, you can return to this notebook to tweak the hyperparameters (and/or the architecture in **model.py**) and re-train your model.

### Question 1

**Question:** Describe your CNN-RNN architecture in detail.  With this architecture in mind, how did you select the values of the variables in Task 1?  If you consulted a research paper detailing a successful implementation of an image captioning model, please provide the reference.

**Answer:** 


### (Optional) Task #2

Note that we have provided a recommended image transform `transform_train` for pre-processing the training images, but you are welcome (and encouraged!) to modify it as you wish.  When modifying this transform, keep in mind that:
- the images in the dataset have varying heights and widths, and 
- if using a pre-trained model, you must perform the corresponding appropriate normalization.

### Question 2

**Question:** How did you select the transform in `transform_train`?  If you left the transform at its provided value, why do you think that it is a good choice for your CNN architecture?

**Answer:** 

### Task #3

Next, you will specify a Python list containing the learnable parameters of the model.  For instance, if you decide to make all weights in the decoder trainable, but only want to train the weights in the embedding layer of the encoder, then you should set `params` to something like:
```
params = list(decoder.parameters()) + list(encoder.embed.parameters()) 
```

### Question 3

**Question:** How did you select the trainable parameters of your architecture?  Why do you think this is a good choice?

**Answer:** 

### Task #4

Finally, you will select an [optimizer](http://pytorch.org/docs/master/optim.html#torch.optim.Optimizer).

### Question 4

**Question:** How did you select the optimizer used to train your model?

**Answer:** 

# Answer 1:
CNN architecure is the resnet50 model as provided in the EncoderRNN. The output of the resnet50 is connected to a fully connected layer whose output dimension is the same as the embedding size of the captions.

RNN is a LSTM whose parameters are chosen after running some simulations on my local machine.
See Answer 3 below on how some of the training parameters were chosen

# Answer 2:
The transform in transform_train is choosen to be the same as provided in code. The input size of 224 X 224 is a standard choice in extracting features from images. Random crop also helps in generating non-perfect images thus making the model more robust.

# Answer 3:

The list of trainable parameters consists of the weights and bias of the final layer in the encoder and all the parameters of the decoder. 


In the encoder, the parameters for the resnet50 architecture are not trained, since they have pretrained to produce feature sets. The final fully connected layer that has has added in this project need to be optimized for this problem and hance considered trainable.


All parameters in the decoder are treated as trainable since these are not optimized for this problem and hance need to trained.  Hence the trainable parameters include all the parameters from and the parameters involved in converting the hidden to output tag.


# Answer 4:
Adam optimizer was chosen. This was based on the discussion in Slack and the papers above. I would like to experiment with other flavors of Optimizer, but is not done yet due to lack of time

In [4]:
import torch
import torch.nn as nn
from torchvision import transforms
import sys
sys.path.append('/opt/cocoapi/PythonAPI')
from pycocotools.coco import COCO
from data_loader import get_loader
from model import EncoderCNN, DecoderRNN
import math


## TODO #1: Select appropriate values for the Python variables below.
batch_size = 64            # batch size
vocab_threshold = 2        # minimum word count threshold
vocab_from_file = True     # if True, load existing vocab file
embed_size = 512           # dimensionality of image and word embeddings
hidden_size = 512          # number of features in hidden state of the RNN decoder
num_epochs = 3             # number of training epochs
save_every = 1             # determines frequency of saving model weights
print_every = 100          # determines window for printing average loss
log_file = 'training_log.txt'       # name of file with saved training loss and perplexity

# (Optional) TODO #2: Amend the image transform below.
transform_train = transforms.Compose([ 
    transforms.Resize(256),                          # smaller edge of image resized to 256
    transforms.RandomCrop(224),                      # get 224x224 crop from random location
    transforms.RandomHorizontalFlip(),               # horizontally flip image with probability=0.5
    transforms.ToTensor(),                           # convert the PIL Image to a tensor
    transforms.Normalize((0.485, 0.456, 0.406),      # normalize image for pre-trained model
                         (0.229, 0.224, 0.225))])

# Build data loader.
data_loader = get_loader(transform=transform_train,
                         mode='train',
                         batch_size=batch_size,
                         vocab_threshold=vocab_threshold,
                         vocab_from_file=vocab_from_file)

# The size of the vocabulary.
vocab_size = len(data_loader.dataset.vocab)

# Initialize the encoder and decoder. 
encoder = EncoderCNN(embed_size)
decoder = DecoderRNN(embed_size, hidden_size, vocab_size)

# Move models to GPU if CUDA is available. 
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
encoder.to(device)
decoder.to(device)

# Define the loss function. 
criterion = nn.CrossEntropyLoss().cuda() if torch.cuda.is_available() else nn.CrossEntropyLoss()

# TODO #3: Specify the learnable parameters of the model.
params = list(encoder.embed.parameters()) + list(decoder.lstm.parameters()) + list(decoder.hidden2Tag.parameters())

# TODO #4: Define the optimizer.
optimizer = torch.optim.Adam(params, lr = 0.001)

# Set the total number of training steps per epoch.
total_step = math.ceil(len(data_loader.dataset.caption_lengths) / data_loader.batch_sampler.batch_size)

Vocabulary successfully loaded from vocab.pkl file!
loading annotations into memory...


  0%|          | 1091/414113 [00:00<01:14, 5518.86it/s]

Done (t=0.81s)
creating index...
index created!
Obtaining caption lengths...


100%|██████████| 414113/414113 [01:04<00:00, 6467.22it/s]


<a id='step2'></a>
## Step 2: Train your Model

Once you have executed the code cell in **Step 1**, the training procedure below should run without issue.  

It is completely fine to leave the code cell below as-is without modifications to train your model.  However, if you would like to modify the code used to train the model below, you must ensure that your changes are easily parsed by your reviewer.  In other words, make sure to provide appropriate comments to describe how your code works!  

You may find it useful to load saved weights to resume training.  In that case, note the names of the files containing the encoder and decoder weights that you'd like to load (`encoder_file` and `decoder_file`).  Then you can load the weights by using the lines below:

```python
# Load pre-trained weights before resuming training.
encoder.load_state_dict(torch.load(os.path.join('./models', encoder_file)))
decoder.load_state_dict(torch.load(os.path.join('./models', decoder_file)))
```

While trying out parameters, make sure to take extensive notes and record the settings that you used in your various training runs.  In particular, you don't want to encounter a situation where you've trained a model for several hours but can't remember what settings you used :).

### A Note on Tuning Hyperparameters

To figure out how well your model is doing, you can look at how the training loss and perplexity evolve during training - and for the purposes of this project, you are encouraged to amend the hyperparameters based on this information.  

However, this will not tell you if your model is overfitting to the training data, and, unfortunately, overfitting is a problem that is commonly encountered when training image captioning models.  

For this project, you need not worry about overfitting. **This project does not have strict requirements regarding the performance of your model**, and you just need to demonstrate that your model has learned **_something_** when you generate captions on the test data.  For now, we strongly encourage you to train your model for the suggested 3 epochs without worrying about performance; then, you should immediately transition to the next notebook in the sequence (**3_Inference.ipynb**) to see how your model performs on the test data.  If your model needs to be changed, you can come back to this notebook, amend hyperparameters (if necessary), and re-train the model.

That said, if you would like to go above and beyond in this project, you can read about some approaches to minimizing overfitting in section 4.3.1 of [this paper](http://ieeexplore.ieee.org/stamp/stamp.jsp?arnumber=7505636).  In the next (optional) step of this notebook, we provide some guidance for assessing the performance on the validation dataset.

In [5]:
import torch.utils.data as data
import numpy as np
import os
import requests
import time

# Open the training log file.
f = open(log_file, 'w')

old_time = time.time()
response = requests.request("GET", 
                            "http://metadata.google.internal/computeMetadata/v1/instance/attributes/keep_alive_token", 
                            headers={"Metadata-Flavor":"Google"})

for epoch in range(1, num_epochs+1):
    
    for i_step in range(1, total_step+1):
        
        if time.time() - old_time > 60:
            old_time = time.time()
            requests.request("POST", 
                             "https://nebula.udacity.com/api/v1/remote/keep-alive", 
                             headers={'Authorization': "STAR " + response.text})
        
        # Randomly sample a caption length, and sample indices with that length.
        indices = data_loader.dataset.get_train_indices()
        # Create and assign a batch sampler to retrieve a batch with the sampled indices.
        new_sampler = data.sampler.SubsetRandomSampler(indices=indices)
        data_loader.batch_sampler.sampler = new_sampler
        
        # Obtain the batch.
        images, captions = next(iter(data_loader))

        # Move batch of images and captions to GPU if CUDA is available.
        images = images.to(device)
        captions = captions.to(device)
        
        # Zero the gradients.
        decoder.zero_grad()
        encoder.zero_grad()
        
        # Pass the inputs through the CNN-RNN model.
        features = encoder(images)
        outputs = decoder(features, captions)
        
        # Calculate the batch loss.
        loss = criterion(outputs.view(-1, vocab_size), captions.view(-1))
        
        # Backward pass.
        loss.backward()
        
        # Update the parameters in the optimizer.
        optimizer.step()
            
        # Get training statistics.
        stats = 'Epoch [%d/%d], Step [%d/%d], Loss: %.4f, Perplexity: %5.4f' % (epoch, num_epochs, i_step, total_step, loss.item(), np.exp(loss.item()))
        
        # Print training statistics (on same line).
        print('\r' + stats, end="")
        sys.stdout.flush()
        
        # Print training statistics to file.
        f.write(stats + '\n')
        f.flush()
        
        # Print training statistics (on different line).
        if i_step % print_every == 0:
            print('\r' + stats)
            
    # Save the weights.
    if epoch % save_every == 0:
        torch.save(decoder.state_dict(), os.path.join('./models', 'decoder-%d.pkl' % epoch))
        torch.save(encoder.state_dict(), os.path.join('./models', 'encoder-%d.pkl' % epoch))

# Close the training log file.
f.close()

 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 12, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [1/6471], Loss: 9.2224, Perplexity: 10121.2366 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 12, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [2/6471], Loss: 9.1285, Perplexity: 9214.4186 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [3/6471], Loss: 9.0528, Perplexity: 8542.4166 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 11, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [4/6471], Loss: 8.9684, Perplexity: 7851.1872 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features sha

Epoch [1/3], Step [37/6471], Loss: 6.9101, Perplexity: 1002.3384 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [38/6471], Loss: 6.8298, Perplexity: 924.9865 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 15, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [39/6471], Loss: 6.8594, Perplexity: 952.8018 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 15, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [40/6471], Loss: 6.6754, Perplexity: 792.6662 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [41/6471], Loss: 6.5484, Perplexity: 698.1236 types **##    torch.cuda.FloatTenso

Epoch [1/3], Step [74/6471], Loss: 4.9051, Perplexity: 134.9790 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 12, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [75/6471], Loss: 5.0022, Perplexity: 148.7448 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 11, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [76/6471], Loss: 5.0771, Perplexity: 160.3120 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 13, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [77/6471], Loss: 4.9186, Perplexity: 136.8094 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 16, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [78/6471], Loss: 4.8791, Perplexity: 131.5167 types **##    torch.cuda.FloatTensor

Epoch [1/3], Step [111/6471], Loss: 4.4359, Perplexity: 84.4319 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 13, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [112/6471], Loss: 4.5656, Perplexity: 96.1210 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 12, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [113/6471], Loss: 4.6223, Perplexity: 101.7299 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [114/6471], Loss: 4.6494, Perplexity: 104.5205 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 12, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [115/6471], Loss: 4.4107, Perplexity: 82.3241 types **##    torch.cuda.FloatTens

Epoch [1/3], Step [148/6471], Loss: 4.3657, Perplexity: 78.7049 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 11, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [149/6471], Loss: 4.3943, Perplexity: 80.9847 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 13, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [150/6471], Loss: 4.4288, Perplexity: 83.8339 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 11, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [151/6471], Loss: 4.5018, Perplexity: 90.1799 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 18, 512]) torch.Size([64, 1, 512])
Epoch [1/3], Step [152/6471], Loss: 4.4069, Perplexity: 82.0156 types **##    torch.cuda.FloatTensor

...

Epoch [3/3], Step [6111/6471], Loss: 2.2824, Perplexity: 9.7997 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 13, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6112/6471], Loss: 2.7209, Perplexity: 15.1947 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 15, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6113/6471], Loss: 2.5393, Perplexity: 12.6706 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6114/6471], Loss: 2.4511, Perplexity: 11.6012 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 11, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6115/6471], Loss: 2.6101, Perplexity: 13.5998 types **##    torch.cuda.FloatTe

Epoch [3/3], Step [6183/6471], Loss: 2.4881, Perplexity: 12.0384 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 13, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6184/6471], Loss: 2.4022, Perplexity: 11.0475 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6185/6471], Loss: 2.6222, Perplexity: 13.7663 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6186/6471], Loss: 2.4424, Perplexity: 11.5010 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 12, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6187/6471], Loss: 2.3457, Perplexity: 10.4407 types **##    torch.cuda.FloatT

Epoch [3/3], Step [6255/6471], Loss: 2.5312, Perplexity: 12.5689 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6256/6471], Loss: 2.4917, Perplexity: 12.0819 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6257/6471], Loss: 2.5568, Perplexity: 12.8947 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 28, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6258/6471], Loss: 3.8307, Perplexity: 46.0943 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6259/6471], Loss: 2.3108, Perplexity: 10.0826 types **##    torch.cuda.FloatT

Epoch [3/3], Step [6327/6471], Loss: 2.3104, Perplexity: 10.0789 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 13, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6328/6471], Loss: 2.1357, Perplexity: 8.4627 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 14, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6329/6471], Loss: 2.5481, Perplexity: 12.7829 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 12, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6330/6471], Loss: 2.4182, Perplexity: 11.2254 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 13, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6331/6471], Loss: 2.4764, Perplexity: 11.8986 types **##    torch.cuda.FloatTe

Epoch [3/3], Step [6399/6471], Loss: 2.5346, Perplexity: 12.6116 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 10, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6400/6471], Loss: 2.7437, Perplexity: 15.5439
 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 15, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6401/6471], Loss: 2.5459, Perplexity: 12.7542 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 10, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6402/6471], Loss: 2.5602, Perplexity: 12.9385 types **##    torch.cuda.FloatTensor torch.cuda.FloatTensor
Embed shape and unsqueeze features shape = *****  torch.Size([64, 12, 512]) torch.Size([64, 1, 512])
Epoch [3/3], Step [6403/6471], Loss: 2.3224, Perplexity: 10.2005 types **##    torch.cuda.Float

<a id='step3'></a>
## Step 3: (Optional) Validate your Model

To assess potential overfitting, one approach is to assess performance on a validation set.  If you decide to do this **optional** task, you are required to first complete all of the steps in the next notebook in the sequence (**3_Inference.ipynb**); as part of that notebook, you will write and test code (specifically, the `sample` method in the `DecoderRNN` class) that uses your RNN decoder to generate captions.  That code will prove incredibly useful here. 

If you decide to validate your model, please do not edit the data loader in **data_loader.py**.  Instead, create a new file named **data_loader_val.py** containing the code for obtaining the data loader for the validation data.  You can access:
- the validation images at filepath `'/opt/cocoapi/images/train2014/'`, and
- the validation image caption annotation file at filepath `'/opt/cocoapi/annotations/captions_val2014.json'`.

The suggested approach to validating your model involves creating a json file such as [this one](https://github.com/cocodataset/cocoapi/blob/master/results/captions_val2014_fakecap_results.json) containing your model's predicted captions for the validation images.  Then, you can write your own script or use one that you [find online](https://github.com/tylin/coco-caption) to calculate the BLEU score of your model.  You can read more about the BLEU score, along with other evaluation metrics (such as TEOR and Cider) in section 4.1 of [this paper](https://arxiv.org/pdf/1411.4555.pdf).  For more information about how to use the annotation file, check out the [website](http://cocodataset.org/#download) for the COCO dataset.

In [ ]:
# (Optional) TODO: Validate your model.